## Importing packages

In [1]:
'''# Record of additions to Jupyter docker's Python packages:
pip install --upgrade pip
pip install lxml
pip install pyxDamerauLevenshtein
pip install google
pip install kmodes
pip install https://github.com/slimkrazy/python-google-places/zipball/master'''

"# Record of additions to Jupyter docker's Python packages:\npip install --upgrade pip\npip install lxml\npip install pyxDamerauLevenshtein"

In [1]:
from bs4 import BeautifulSoup
import pandas, csv, numpy as np
import urllib, requests
import os, os.path, re
from glob import glob

# for comparing strings in order to match elements between lists:
from pyxdameraulevenshtein import normalized_damerau_levenshtein_distance as dldist
from pyxdameraulevenshtein import normalized_damerau_levenshtein_distance_ndarray as dldistarray

#from lxml import html, etree
# from requests.auth import HTTPBasicAuth, HTTPDigestAuth
# import nbimporter #need to pip install this
# import EncapsulatedSchoolObject as school

In [2]:
print(dldist('smtih', 'smith'))  # expected result: 0.2

array = np.array(['test1', 'test12', 'test123'])
print('\n', dldistarray('test', array))  # expected result: [0.2, 0.33333334, 0.42857143]
print('\n', min(dldistarray('test', array)))

0.20000000298023224

 [ 0.2         0.33333334  0.42857143]

 0.2


## Reading in data

In [3]:
sample = [] # make empty list to store the dictionaries in
with open('../charter_URLs_Apr17.csv', 'r', encoding = 'Latin-1')\
as csvfile: # open file                      
    reader = csv.DictReader(csvfile) # create a reader
    for row in reader: # loop through rows
        sample.append(row) # append each row to the list

In [4]:
# Take a look at the first entry's contents and the variables list in our sample (a list of dictionaries)
print(sample[1]['SEARCH'], "\n", sample[1]["OLD_URL"], "\n")
print(sample[1].keys())

POLK STATE COLLEGE COLLEGIATE HIGH SCHOOL 3425 WINTER LK RD LAC1200, WINTER HAVEN, FL 33881 
 https://www.polk.edu/charter-high-schools/ 

dict_keys(['OLD_URL', 'SCH_NAME', 'SEARCH', 'NCESSCH', 'ADDRESS', 'STABR', 'MANUAL_URL'])


In [5]:
'''# read in data
df = pandas.read_excel('micro-sample_MANUAL_Apr17_rev3.xlsx')

#get the values from the URL column (stored as list)
links = df['URL'].values

# Input test URL
url = links[0]
url
'''

"# read in data\ndf = pandas.read_excel('micro-sample_MANUAL_Apr17_rev3.xlsx')\n\n#get the values from the URL column (stored as list)\nlinks = df['URL'].values\n\n# Input test URL\nurl = links[0]\nurl\n"

In [6]:
'''for i in $(find -maxdepth 1 -type d); do echo -n "$i "; find $i -type f | wc -l; done  | grep ' 1$'  | wc -l
   55  find www.polk.edu/
   56  find | head
   57  find | head -n 100
   58  find
   59  find www.hustonacademy.com/
   60  find www.hustonacademy.com/ -type d
   61  find www.hustonacademy.com/ -maxdepth 1 -type d
   62  find www.hustonacademy.com/ -maxdepth 0 -type d
   63  find www.hustonacademy.com/ -maxdepth 1 -type d
   64  find www.hustonacademy.com/ -maxdepth 2 -type d
   65  find www.hustonacademy.com/ -maxdepth 3 -type d
   66  find -maxdepth 1 -type d
   67  l s-la
   68  ls -la
   69  for i in $(find -maxdepth 1 -type d); do echo -n "$i "; find $i -type f | wc -l; done  | grep ' 1$'  | wc -l
   70  for i in $(find -maxdepth 1 -type d); do echo -n "$i "; find $i -type f | wc -l; done  | grep ' 1$'  
   71  for i in $(find -maxdepth 1 -type d); do echo -n "$i "; find $i -type f | wc -l; done  | grep -v ' 1$'

!find .  -maxdepth 1 -type d | wc -l

!find /tmp  -maxdepth 1 -type d | wc -l'''

'for i in $(find -maxdepth 1 -type d); do echo -n "$i "; find $i -type f | wc -l; done  | grep \' 1$\'  | wc -l\n   55  find www.polk.edu/\n   56  find | head\n   57  find | head -n 100\n   58  find\n   59  find www.hustonacademy.com/\n   60  find www.hustonacademy.com/ -type d\n   61  find www.hustonacademy.com/ -maxdepth 1 -type d\n   62  find www.hustonacademy.com/ -maxdepth 0 -type d\n   63  find www.hustonacademy.com/ -maxdepth 1 -type d\n   64  find www.hustonacademy.com/ -maxdepth 2 -type d\n   65  find www.hustonacademy.com/ -maxdepth 3 -type d\n   66  find -maxdepth 1 -type d\n   67  l s-la\n   68  ls -la\n   69  for i in $(find -maxdepth 1 -type d); do echo -n "$i "; find $i -type f | wc -l; done  | grep \' 1$\'  | wc -l\n   70  for i in $(find -maxdepth 1 -type d); do echo -n "$i "; find $i -type f | wc -l; done  | grep \' 1$\'  \n   71  for i in $(find -maxdepth 1 -type d); do echo -n "$i "; find $i -type f | wc -l; done  | grep -v \' 1$\'\n\n!find .  -maxdepth 1 -type d | 

## Configuring environment for parsing text

In [5]:
data_loc = "/home/jovyan/work/mirror/" # Point to where HTML has been captured

In [6]:
# For different ways of parsing the text, identify elements we know we DON'T want (to rip out):
junkName = ['style', 'script', '[document]', 'head', 'title', 'meta', 'a', 'label', 'footer']

# And also elements we know we DO want (to keep):
correctName = ['p', 'li', 'table', 'ul', 'ol', 'h1', 'h2', 'h3', 'h4', 'h5', 'h6', 'h7', 'h8', 'h9', 'h10']

In [7]:
os.getcwd()

'/home/jovyan/work/Charter-school-identities/scripts'

In [8]:
testurl = "https://acaciamiddle.org/about/our-mission-and-philosophy"

try:
    testfile = "/home/jovyan/work/mirror/acaciamiddle.org/about/our-mission-and-philosophy.html"
    testfolder = "/home/jovyan/work/mirror/acaciamiddle.org/"
    soup = BeautifulSoup(open(testfile), "lxml")
except:
    html_page = urllib.request.urlopen(testurl)
    soup = BeautifulSoup(html_page, "lxml")

ptags = soup.find_all("p")
print(ptags)

[<p>The mission of Acacia Middle Charter School is to provide a nurturing and challenging learning community to the greater Stockton area. Students will experience learning in ways that will allow them to both understand and improve their world. Our exceptional teachers inspire students to seek deep, meaningful understanding; to develop strong academic skills; and to become creative and independent thinkers. A rapidly changing global environment requires that Acacia students acquire knowledge and develop 21<sup>st</sup> century skills, while learning to define and solve problems creatively. Acacia Middle cultivates compassion, fairness, respect, and individuality within a community that celebrates diversity, authenticity, and service.</p>, <p>Acacia Middle embodies the following key assumptions in philosophy and daily practice:</p>, <p> </p>, <p> </p>, <p> </p>, <p><span style="font-size:14px;"><strong>(209) 956-2182 Fax</strong></span></p>, <p>©Tri Valley Learning Corporation - All Ri

In [11]:
'''# This gives only the VISIBLE text on the web page:

from bs4.element import Comment
data = soup.findAll(text=True) 

def visible(element):
    if element.parent.name in ['style', 'script', '[document]', 'head', 'title', 'meta']:
        return False
    elif isinstance(element, Comment):
        return False
    return True

# Alternative way of ripping out comments (line 3 of "visible" function above):
# elif re.match('<!--.*-->', str(element.encode('utf-8'))):

visible_texts = list(filter(visible, data))
visible_texts'''

'# This gives only the VISIBLE text on the web page:\n\nfrom bs4.element import Comment\ndata = soup.findAll(text=True) \n\ndef visible(element):\n    if element.parent.name in [\'style\', \'script\', \'[document]\', \'head\', \'title\', \'meta\']:\n        return False\n    elif isinstance(element, Comment):\n        return False\n    return True\n\n# Alternative way of ripping out comments (line 3 of "visible" function above):\n# elif re.match(\'<!--.*-->\', str(element.encode(\'utf-8\'))):\n\nvisible_texts = list(filter(visible, data))\nvisible_texts'

In [17]:
def format_string(newstring):
    
    '''This removes extraneous characters "b" and "'" at beginning and end of strings.
    Useful to parsing text scraped from HTML files.'''
    
    if   (newstring[:2] == "b'" and
          newstring[-1] == "'"):      
          newstring = newstring[2:-1] #re.sub("b'.*?", "", newstring[:-1])
            
    elif (newstring[0] == "'" and
          newstring[-1] == "'"):
          newstring = newstring[1:-1]
            
    elif (newstring[0] == "'"):
          newstring = newstring[1:]
            
    elif (newstring[-1] == "'"):
          newstring = newstring[:-1]
            
    elif (newstring[:2] == "b'"):
          newstring = newstring[2:]
    
    elif   (newstring[:2] == 'b"' and
          newstring[-1] == '"'):      
          newstring = newstring[2:-1] #re.sub("b'.*?", "", newstring[:-1])
            
    elif (newstring[0] == '"' and
          newstring[-1] == '"'):
          newstring = newstring[1:-1]
            
    elif (newstring[0] == '"'):
          newstring = newstring[1:]
            
    elif (newstring[-1] == '"'):
          newstring = newstring[:-1]
            
    elif (newstring[:2] == 'b"'):
          newstring = newstring[2:]
    
    else:
        pass
    
    return(newstring)

In [13]:
def rip_text(fname, junk_list):

    '''This method of grabbing the visible text from a .html file first converts the HTML to a BeautifulSoup object, 
    then it rips out all script and style elements with tags identified through junkName_list. 
    It finishes by taking out the newlines and outputting a single string of all the visible text from the .html file.'''

    soup = BeautifulSoup(open(fname), "lxml")

    for script in soup(junk_list):   # loop through every junk tag in soup
        script.extract()    # rip out all script and style elements

    ripped_text = soup.get_text() # get text
    # print(ripped_text.encode('utf-8'))   # for checking work

    # break into lines and remove leading and trailing space on each:
    lines = (line.strip() for line in ripped_text.splitlines())
    # break multi-headlines into a line each:
    chunks = (phrase.strip() for line in lines for phrase in line.split("  "))
    # drop blank lines
    ripped_textc = ' '.join(chunk for chunk in chunks if chunk)

    return(ripped_textc.encode('utf-8'))   # return output

In [86]:
# Testing out the parsing and formatting functions:
testtext = format_string(str(rip_text(testfile, junkName)))
print(testtext) # This looks good!

Main menu Our Mission and Philosophy English Our Mission: The mission of Acacia Middle Charter School is to provide a nurturing and challenging learning community to the greater Stockton area. Students will experience learning in ways that will allow them to both understand and improve their world.\xc2\xa0Our exceptional teachers inspire students to seek deep, meaningful understanding; to develop strong academic skills; and to become creative and independent thinkers. A rapidly changing global environment requires that Acacia students acquire knowledge and develop 21st century skills, while learning to define and solve problems creatively. Acacia Middle cultivates compassion, fairness, respect, and individuality within a community that celebrates diversity, authenticity, and service. Our Philosophy: Acacia Middle embodies the following key assumptions in philosophy and daily practice: learning is the young person\xe2\x80\x99s pathway to personal growth school should be both challenging

In [14]:
def keep_text(fname, correctName_list):

    '''This method of grabbing the visible text from a .html file first converts the HTML to a BeautifulSoup object, 
    then it keeps only those elements with tags identified through correctName_list. 
    It finishes by taking out the newlines and outputting a single string of all the visible text from the .html file.'''

    soup = BeautifulSoup(open(fname), "lxml")

    for script in soup:   # loop through every tag in the soup object
        if script not in soup(correctName_list):
            script.extract()    # keep only the good tags
        
    good_text = soup.get_text() # get text
    # print(ripped_text.encode('utf-8'))   # for checking work

    # break into lines and remove leading and trailing space on each:
    lines = (line.strip() for line in good_text.splitlines())
    # break multi-headlines into a line each:
    chunks = (phrase.strip() for line in lines for phrase in line.split("  "))
    # drop blank lines
    good_textc = ' '.join(chunk for chunk in chunks if chunk)

    print("\n", good_textc.encode('utf-8'))   # print output

In [15]:
keep_text(testfile, correctName)


 b'Our Mission and Philosophy | Acacia Middle Charter School <!--//--><![CDATA[//><!-- jQuery.extend(Drupal.settings, {"basePath":"\\/","pathPrefix":"","ajaxPageState":{"theme":"lvcp","theme_token":"Vg8IZ5kokc7eZAY3hPUqB-Td53PVSK-EF5s11P2_Jdg","js":{"misc\\/jquery.js":1,"misc\\/jquery.once.js":1,"misc\\/drupal.js":1,"sites\\/all\\/libraries\\/colorbox\\/jquery.colorbox-min.js":1,"sites\\/all\\/modules\\/colorbox\\/js\\/colorbox.js":1,"sites\\/all\\/modules\\/colorbox\\/styles\\/default\\/colorbox_style.js":1,"sites\\/all\\/modules\\/field_group\\/field_group.js":1,"sites\\/all\\/themes\\/noodle\\/base\\/noodle.js":1,"sites\\/all\\/libraries\\/superfish\\/superfish.js":1,"sites\\/all\\/libraries\\/superfish\\/jquery.hoverIntent.minified.js":1,"sites\\/all\\/libraries\\/superfish\\/supersubs.js":1,"sites\\/all\\/modules\\/superfish\\/superfish.js":1},"css":{"modules\\/system\\/system.base.css":1,"modules\\/system\\/system.menus.css":1,"modules\\/system\\/system.messages.css":1,"modules\

In [16]:
bool(BeautifulSoup(open(testfile), "html.parser").find())==True

True

In [14]:
folder_list = next(os.walk(data_loc))[1]
print(len(folder_list))
folder_list

# list(set(folder_list).intersection(URL_list))

276


['www.stcroixprep.org',
 'www.kawaikini.com',
 'www.confluenceacademy.com',
 'www.shawanoschools.com',
 'www.performanceacademies.com',
 'www.sunvalleycharterschool.com',
 'highlandfreeschool.org',
 'www.janesville.k12.wi.us',
 'www.aascalifornia.org',
 'life.hartlake.org',
 'evolutionacademy.org',
 'www.bcclc.com',
 'www.hustonacademy.com',
 'www.mnohs.org',
 'www.rivervalleyhigh.org',
 'www.nycmcs.org',
 'www.providencehall.com',
 'excellenceboys.uncommonschools.org',
 'www.spacharter.org',
 'www.northwoodcs.org',
 'ca01902906.schoolwires.net',
 'www.lakecountryacademy.com',
 'paintedrockacademy.com',
 'innovationsacademy.org',
 'www.sage-academy.org',
 'www.newcastle.k12.ca.us',
 'www.pvcics.org',
 'bakercharters.org',
 'www.wattslearningcenter.org',
 'rvms.vail.k12.az.us',
 'www.magellancharter.org',
 'www.leadingedgeacademy.com',
 'enlaceacademy.org',
 'efcps.org',
 'www.palcs.org',
 'www.ivyprepacademy.org',
 'responsiveed.com',
 'www.minisacademy.org',
 'www.kippmetroatlanta.org

In [18]:
def matching_folder(data_location, match_var, list_folders):
    
    '''This function finds the folder name in data_loc closest to match_var.
    It matches based on normalized character differences, using the pyxDamerauLevenshtein library.
    This works whether the folders have been named according to SCH_NAME, URL, or something else.'''
    
    # Make array of normalized distances between match_var and each directory name
    distarray = dldistarray(match_var, np.array(list_folders))
    
    # Find index of that array element with the lowest normalized distance to match_var, i.e. index of the best match
    #print("Finding best match out of " + str(len(distarray)) + " options...")
    index_match = list(distarray).index(min(distarray))
    
    # TO DO: If min(distarray)>.5, then search using the given match_var WITHOUT 
    # everything past the last "/" (until str following "http://")
    
    # Use index_match to identify folder in list_folders that best matches match_var
    name_folder = list_folders[index_match]
    
    # Remove result from list_folders in order to return UNIQUE matches--currently low reliability
    # print("Removing " + name_folder + " from list of folders...\n")
    # list_folders.remove(name_folder)
    
    # Return best match, with a printed accuracy check of matching algorithm
    print("Best folder match is " + str(name_folder) + " with normalized distance of " + str(min(distarray)) + "!\n")
    return(name_folder)

In [22]:
# Make list of directories (containing HTML) in data_location
folder_list = next(os.walk(data_loc))[1] 

# Assign a folder to each school in sample using the matchin_folder function

k=0 # initialize iterator

for school in sample: # loop through sample
    print("Finding folder for " + str(k) + " of " + str(len(sample)) + ", " + school["SCH_NAME"] + ", \nlisted " + str(school["MANUAL_URL"]) + "...")
    
    if school["MANUAL_URL"] != '':
        
        try:
            school["folder_name"] = matching_folder(data_loc, school["MANUAL_URL"], folder_list)
        except:
            print("ERROR!")
            school["folder_name"] = ''
    
    else:
        print("Nothing to match on!")
        school["folder_name"] = ''
    
    k+=1

Finding folder for 0 of 6752, Richland Two Charter High, 
listed https://www.richland2.org/charterhigh/...
Best folder match is www.richland2.org with normalized distance of 0.552632!

Finding folder for 1 of 6752, POLK STATE COLLEGE COLLEGIATE HIGH SCHOOL, 
listed https://www.polk.edu/lakeland-gateway-to-college-high-school/...
Best folder match is www.performanceacademies.com with normalized distance of 0.754098!

Finding folder for 2 of 6752, River City Scholars Charter Academy, 
listed https://www.nhaschools.com/schools/rivercity/Pages/default.aspx...
Best folder match is www.nhaschools.com with normalized distance of 0.714286!

Finding folder for 3 of 6752, Detroit Enterprise Academy, 
listed https://www.nhaschools.com/schools/detroitenterprise...
Best folder match is www.nhaschools.com with normalized distance of 0.653846!

Finding folder for 4 of 6752, MINISINAAKWAANG LEADERSHIP ACADEMY, 
listed https://www.minisacademy.org...
Best folder match is www.minisacademy.org with norma

Best folder match is www.swschools.org with normalized distance of 0.32!

Finding folder for 46 of 6752, SOUTHWEST PREPARATORY SCHOOL-NORTHWEST, 
listed http://www.swprep.org/...
Best folder match is www.swprep.org with normalized distance of 0.363636!

Finding folder for 47 of 6752, Sun Valley Charter School, 
listed http://www.sunvalleycharterschool.com/...
Best folder match is www.sunvalleycharterschool.com with normalized distance of 0.210526!

Finding folder for 48 of 6752, Sunny Wolf Charter School, 
listed http://www.sunnywolfcharterschool.com/...
Best folder match is www.sunvalleycharterschool.com with normalized distance of 0.368421!

Finding folder for 49 of 6752, SUNCOAST SCHOOL FOR INNOVATIVE STUDIES, 
listed http://www.suncoastschool.org/...
Best folder match is www.suncoastschool.org with normalized distance of 0.266667!

Finding folder for 50 of 6752, Kaizen Education Foundation dba Summit High School, 
listed http://www.summiths.com/...
Best folder match is www.summiths

Finding folder for 440 of 6752, Adams Traditional Academy, 
listed ...
Nothing to match on!
Finding folder for 441 of 6752, ADDENBROOKE CLASSICAL ACADEMY, 
listed ...
Nothing to match on!
Finding folder for 442 of 6752, Adelante Charter, 
listed ...
Nothing to match on!
Finding folder for 443 of 6752, Advanced Learning Academy of Wisconsin, 
listed ...
Nothing to match on!
Finding folder for 444 of 6752, Advanced Math and Science Academy Charter School, 
listed ...
Nothing to match on!
Finding folder for 445 of 6752, Advanced Technology Academy, 
listed ...
Nothing to match on!
Finding folder for 446 of 6752, ADVANCED VIRTUAL ACADEMY, 
listed ...
Nothing to match on!
Finding folder for 447 of 6752, ADVANTAGE ACADEMY, 
listed ...
Nothing to match on!
Finding folder for 448 of 6752, ADVANTAGE ACADEMY MIDDLE SCHOOL, 
listed ...
Nothing to match on!
Finding folder for 449 of 6752, ADVANTAGE ACADEMY OF HILLSBOROUGH, 
listed ...
Nothing to match on!
Finding folder for 450 of 6752, ADVANTAGE 

Nothing to match on!
Finding folder for 1967 of 6752, e3 Civic High, 
listed ...
Nothing to match on!
Finding folder for 1968 of 6752, eAchieve Academy - Wisconsin, 
listed ...
Nothing to match on!
Finding folder for 1969 of 6752, eAchieve Elementary, 
listed ...
Nothing to match on!
Finding folder for 1970 of 6752, Eagle Academy Charter School, 
listed ...
Nothing to match on!
Finding folder for 1971 of 6752, Eagle Academy PCS Eagle Center at McGogney, 
listed ...
Nothing to match on!
Finding folder for 1972 of 6752, Eagle Academy PCS New Jersey Avenue Campus, 
listed ...
Nothing to match on!
Finding folder for 1973 of 6752, EAGLE ARTS ACADEMY, 
listed ...
Nothing to match on!
Finding folder for 1974 of 6752, Eagle Charter School, 
listed ...
Nothing to match on!
Finding folder for 1975 of 6752, EAGLE College Prep, 
listed ...
Nothing to match on!
Finding folder for 1976 of 6752, EAGLE COLLEGE PREP ENDEAVOR, 
listed ...
Nothing to match on!
Finding folder for 1977 of 6752, EAGLE Colle

Nothing to match on!
Finding folder for 3499 of 6752, KIPP INTREPID PREPARATORY SCHOOL, 
listed ...
Nothing to match on!
Finding folder for 3500 of 6752, KIPP King Collegiate High, 
listed ...
Nothing to match on!
Finding folder for 3501 of 6752, KIPP LEGACY PREPARATORY SCHOOL, 
listed ...
Nothing to match on!
Finding folder for 3502 of 6752, KIPP LIBERATION COLLEGE PREP, 
listed ...
Nothing to match on!
Finding folder for 3503 of 6752, KIPP Los Angeles College Preparatory, 
listed ...
Nothing to match on!
Finding folder for 3504 of 6752, KIPP McDonogh 15 School for the Creative Arts, 
listed ...
Nothing to match on!
Finding folder for 3505 of 6752, KIPP Memphis Academy Elementary, 
listed ...
Nothing to match on!
Finding folder for 3506 of 6752, KIPP Memphis Collegiate Elementary, 
listed ...
Nothing to match on!
Finding folder for 3507 of 6752, KIPP Memphis Collegiate High School, 
listed ...
Nothing to match on!
Finding folder for 3508 of 6752, KIPP Memphis Collegiate Middle, 
liste

Nothing to match on!
Finding folder for 4925 of 6752, Plainview Academic Charter Academy, 
listed ...
Nothing to match on!
Finding folder for 4926 of 6752, PLATO ACADEMY CHARTER SCHOOL TARPON SPRINGS, 
listed ...
Nothing to match on!
Finding folder for 4927 of 6752, PLATO ACADEMY CLEARWATER, 
listed ...
Nothing to match on!
Finding folder for 4928 of 6752, PLATO ACADEMY LARGO CHARTER SCHOOL, 
listed ...
Nothing to match on!
Finding folder for 4929 of 6752, PLATO ACADEMY OF ST.PETERSBURG, 
listed ...
Nothing to match on!
Finding folder for 4930 of 6752, PLATO ACADEMY PALM HARBOR CHARTER SCHOOL, 
listed ...
Nothing to match on!
Finding folder for 4931 of 6752, PLATO SEMINOLE, 
listed ...
Nothing to match on!
Finding folder for 4932 of 6752, PLATTE RIVER CHARTER ACADEMY, 
listed ...
Nothing to match on!
Finding folder for 4933 of 6752, PLC Arts Academy at Scottsdale  Inc., 
listed ...
Nothing to match on!
Finding folder for 4934 of 6752, Pleasant Community Digital, 
listed ...
Nothing to 

Finding folder for 6176 of 6752, Trivium Charter, 
listed ...
Nothing to match on!
Finding folder for 6177 of 6752, Trix Elementary, 
listed ...
Nothing to match on!
Finding folder for 6178 of 6752, Trotwood Fitness & Prep Acad, 
listed ...
Nothing to match on!
Finding folder for 6179 of 6752, TRUE NORTH ROCHESTER PREP CHARTER SCHOOL-WEST CAMPUS, 
listed ...
Nothing to match on!
Finding folder for 6180 of 6752, TRUE NORTH ROCHESTER PREPARATORY CHARTER SCHOOL (THE), 
listed ...
Nothing to match on!
Finding folder for 6181 of 6752, TRUE NORTH TROY PREPARATORY CHARTER SCHOOL, 
listed ...
Nothing to match on!
Finding folder for 6182 of 6752, Truebright Science Academy CS, 
listed ...
Nothing to match on!
Finding folder for 6183 of 6752, TSU CHARTER LAB SCH, 
listed ...
Nothing to match on!
Finding folder for 6184 of 6752, TUACAHN HIGH SCHOOL FOR THE PERFORMING ARTS, 
listed ...
Nothing to match on!
Finding folder for 6185 of 6752, Tucson Collegiate Prep, 
listed ...
Nothing to match on!
Fi

## Parsing soup for ALL TEXT

In [19]:
# This is how we add together the text from all the HTML files:
print('\n\n\n'.join([format_string(str(testtext)), format_string("b'Here's another example of school site text.")]))

NameError: name 'testtext' is not defined

In [20]:
def parse_alltext(data_location, folder_name, URL_var, junk_list): 
    
    # Note: Need to sort folders (in data_location) and schools (in list_of_dicts) on SAME LIST of URLs!
    # can index folder location to dictionary because dict["URL"]=folder_name!
    
    print("Parsing folder " + str(folder_name) + "...")
    
    folder_path = data_location + folder_name + "/" # Create folder path using data directory and folder name
    all_text = "" # Initialize big string of website text
    parsed = [] # Initialize list of parsed HTML files
        
    for fname in glob(folder_path + "**", recursive=True): # Loop through each file in the directory
        
        try:
            
            if bool(BeautifulSoup(open(fname), "html.parser").find())==True: # Check if file has HTML; if so, then parse it!
                #print("Parsing HTML in " + fname + "...")
                soup = BeautifulSoup(open(fname), "lxml")
                
                ftext = rip_text(fname, junk_list) # extract all text from file, excluding style, etc. elements defined in junk_list
                
                all_text = "\n\n\n".join([str(all_text), format_string(str(ftext))]) # add ripped text from file to big string, all_text
                
                parsed.append(str(fname)) # add file name to list of files that have been parsed
            
            else:
                pass
                
        except:
            pass
        
    print("Success! Returning all website text from " + str(URL_var) + "...\n")
    return(all_text, parsed)
        
        
    # look in each folder for .html, read in the text, sub ' for b' if needed at start string
    # join together all the text strings, add that as value to school dict, analyze as before.
    # keep out all sites with only ONE HTML file

In [23]:
# Parse text from website for each school in sample using the parse_text function

k=0 # initialize iterator

for school in sample[:1]: # loop through sample
    print("Parsing text for " + str(k) + " of " + str(len(sample)) + ", " + school["SCH_NAME"] + ", \nlisted " + str(school["MANUAL_URL"]) + "...")
    
    if school["folder_name"] != '':
        
        try:
            school["parsed_files"] = []
            school["alltext"], school["parsed_files"] = \
            parse_alltext(data_loc, school["folder_name"], school["MANUAL_URL"], junkName)
        except:
            print("ERROR!")
            school["all_text"] = ''
    
    else:
        print("No folder of scraped web data to parse!")
        school["alltext"] = ''
    
    k+=1


# print(sample[0]["alltext"])

Parsing text for 0 of 6752, Richland Two Charter High, 
listed https://www.richland2.org/charterhigh/...
Parsing folder www.richland2.org...
Success! Returning all website text from https://www.richland2.org/charterhigh/...



In [89]:
print(sample[0]["alltext"])




You may be trying to access this site from a secured browser on the server. Please enable scripts and reload this page. This page location is: Pontiac Elementary School Default Teams Information News & Announcements Thursday, April 27 - Summer Camps & Activities Thursday, April 20 - IMPORTANT TESTING DATES \xe2\x80\x8bMay 9- SC Ready ELA 1May 10- SC Ready ELA 2May 11- SC Ready MathMay 16- SC PASS ScienceMay 17- SC PASS Social StudiesMay 22- State Field Testing (5th only)May 25- State Filed Testing\xc2\xa0\xe2\x80\x8b Calendar of Events 5/9/2017 8:30 AMSC READY ELA 15/10/2017 8:30 AMSC READY ELA 25/11/2017 8:30 AMSC READY MATH5/16/2017 8:30 AMSC PASS Science5/17/2017 8:30 AMSC PASS TESTING Social Studies5/18/2017 6:00 PMSkate Night5/19/2017 8:00 AMField Day5/22/2017 8:30 AMState Field Testing(5th only)5/23/2017 6:30 PMFifth Grade Recognition5/24/2017 8:30 AMVehicle/Career Day1 - 10View in Web Browser/pe/_layouts/VisioWebAccess/VisioWebAccess.aspx?listguid={ListId}&itemid={ItemId}&Def

In [90]:
print(len(sample[0]["parsed_files"]))

1287


## Parsing soup for keywords

In [9]:
# Define lists of keywords for each category of interest, used to group the text
mission = ['mission',' vision ', 'vision:', 'mission:', 'our purpose', 'our ideals', 'ideals:', 'our cause', 'cause:', 'goals', 'objective']
curriculum = ['curriculum', 'curricular', 'program', 'method', 'pedagogy', 'pedagogical', 'approach', 'model', 'system', 'structure']
philosophy = ['philosophy', 'philosophical', 'beliefs', 'believe', 'principles', 'creed', 'credo', 'value',  'moral', 'Values']
history = ['history', 'our story', 'the story', 'school story', 'background', 'founding', 'founded', 'established', 'establishment', 'our school began', 'we began', 'doors opened', 'school opened']
general =  ['about us', 'our school', 'who we are', 'overview', 'general information', 'our identity', 'profile', 'highlights']

keyValues = [mission, curriculum, philosophy, history, general]
nodeParams = ['mission', 'curriculum', 'philosophy', 'history', 'general']

In [10]:
# This helper function creates a list of tags (with text) for a given keyWord:
def findTags(soup, keyWord):
    tagList = []
        
    for elem in soup(text=re.compile(keyWord)):
        tagList.append(elem.parent)
            
    return tagList

In [12]:
mission_tags = findTags(soup, "mission")
mission_tags

'[<p>The mission of Acacia Middle Charter School is to provide a nurturing and challenging learning community to the greater Stockton area. Students will experience learning in ways that will allow them to both understand and improve their world.\xa0Our exceptional teachers inspire students to seek deep, meaningful understanding; to develop strong academic skills; and to become creative and independent thinkers. A rapidly changing global environment requires that Acacia students acquire knowledge and develop 21<sup>st</sup> century skills, while learning to define and solve problems creatively. Acacia Middle cultivates compassion, fairness, respect, and individuality within a community that celebrates diversity, authenticity, and service.</p>]'

In [87]:
def parse_keytext(data_location, folder_name, URL_var, junk_list): 
    
    # Note: Need to sort folders (in data_location) and schools (in list_of_dicts) on SAME LIST of URLs!
    # can index folder location to dictionary because dict["URL"]=folder_name!
    
    print("Parsing folder " + str(folder_name) + "...")
    
    folder_path = data_location + folder_name + "/" # Create folder path using data directory and folder name
    all_text = "" # Initialize big string of website text
    parsed = [] # Initialize list of parsed HTML files
        
    for fname in glob(folder_path + "**", recursive=True): # Loop through each file in the directory
        
        try:
            
            if bool(BeautifulSoup(open(fname), "html.parser").find())==True: # Check if file has HTML; if so, then parse it!
                #print("Parsing HTML in " + fname + "...")
                soup = BeautifulSoup(open(fname), "lxml")
                
                ftext = rip_text(fname, junk_list) # extract all text from file, excluding style, etc. elements defined in junk_list
                
                all_text = "\n\n\n".join([str(all_text), format_string(str(ftext))]) # add ripped text from file to big string, all_text
                
                parsed.append(str(fname)) # add file name to list of files that have been parsed
            
            else:
                pass
                
        except:
            pass
        
    print("Success! Returning all website text from " + str(URL_var) + "...\n")
    return(all_text, parsed)
        
        
    # look in each folder for .html, read in the text, sub ' for b' if needed at start string
    # join together all the text strings, add that as value to school dict, analyze as before.
    # keep out all sites with only ONE HTML file

In [88]:
# Parse text from website for each school in sample using the parse_text function

k=0 # initialize iterator

for school in sample[:1]: # loop through sample
    print("Parsing text for " + str(k) + " of " + str(len(sample)) + ", " + school["SCH_NAME"] + ", \nlisted " + str(school["MANUAL_URL"]) + "...")
    
    if school["folder_name"] != '':
        
        try:
            school["parsed_files"] = []
            school["alltext"], school["parsed_files"] = \
            parse_alltext(data_loc, school["folder_name"], school["MANUAL_URL"], junkName)
        except:
            print("ERROR!")
            school["all_text"] = ''
    
    else:
        print("No folder of scraped web data to parse!")
        school["alltext"] = ''
    
    k+=1


# print(sample[0]["alltext"])

Parsing text for 0 of 6752, Richland Two Charter High, 
listed https://www.richland2.org/charterhigh/...
Parsing folder www.richland2.org...
Success! Returning all website text from https://www.richland2.org/charterhigh/...




You may be trying to access this site from a secured browser on the server. Please enable scripts and reload this page. This page location is: Pontiac Elementary School Default Teams Information News & Announcements Thursday, April 27 - Summer Camps & Activities Thursday, April 20 - IMPORTANT TESTING DATES \xe2\x80\x8bMay 9- SC Ready ELA 1May 10- SC Ready ELA 2May 11- SC Ready MathMay 16- SC PASS ScienceMay 17- SC PASS Social StudiesMay 22- State Field Testing (5th only)May 25- State Filed Testing\xc2\xa0\xe2\x80\x8b Calendar of Events 5/9/2017 8:30 AMSC READY ELA 15/10/2017 8:30 AMSC READY ELA 25/11/2017 8:30 AMSC READY MATH5/16/2017 8:30 AMSC PASS Science5/17/2017 8:30 AMSC PASS TESTING Social Studies5/18/2017 6:00 PMSkate Night5/19/2017 8:00 AMField Day5/22/2

## BETA/ FOR REFERENCE (mostly from this notebook)

In [ ]:
## Create HTML soup
# AKCAN'S VERSION:
html_page = urllib.request.urlopen(url)
soup = BeautifulSoup(html_page, "lxml")

# THAO'S VERSION:
html_page = requests.get(url, auth=HTTPDigestAuth('user', 'pass'), headers= {'User-Agent':"Mozilla/5.0 (Macintosh; Intel Mac OS X 10_11_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/56.0.2924.87 Safari/537.36"})
soup = BeautifulSoup(html_page.text, "lxml")

In [ ]:
#(self, url, nodeParams, keyValues)


#creating a list of all the keyword lists
#keyValues = [mission, curriculum, philosophy, history, target, resources, orgfactor]
keyValues = [mission, curriculum, philosophy, history, general]

#creating a list of key names for the JSON node that correspond to the keyValues list
#nodeParams = ['mission', 'curriculum', 'philosophy', 'history', 'target', 'resources' , 'organizational_factors']
nodeParams = ['mission', 'curriculum', 'philosophy', 'history', 'general']
testedLinks = {}

#print(links[0])



#constructor = school.WebsiteData('https://www.richland2.org/charterhigh/', nodeParams, keyValues)
#constructor.createJsonNode()
#print(constructor.URL)

def tester(links, keyValues, nodeParams):
    testedLinks[links[5]] = school.WebsiteData(links[5], nodeParams, keyValues).createJsonNode()
    #for i in range(5, 6):
        #testedLinks[links[i]] = school.WebsiteData(links[i], nodeParams, keyValues).createJsonNode()
tester(links, keyValues, nodeParams)

## TESTING (from EncapsulatedSchoolObject.ipynb)

In [ ]:
#Finds all tags within a BeautifulSoup object that's text contains a certain keyword and returns a list of these tags.
def findTags(soup, keyWord):
    tagList = []
        
    for elem in soup(text=re.compile(keyWord)):
        tagList.append(elem.parent)
            
    return tagList

In [ ]:
#Utilizes a BeautifulSoup object (soup) to scrape all text that contains the given keyword. Filters for certain tags and does
#not take text from solely header (h) tags, instead takes text from next filtered tag after the header.  
def keyWordScraper(soup, keyWord):
    searchTxt = ''
    correctName = ['p', 'li', 'table', 'ul', 'ol']
    tagList = findTags(soup, keyWord)
    #print(tagList)
    
    #This loop goes through each tag and rips the text from that tag. If that tag is a header, then the text from the next 
    #useful tag is ripped instead. All text is saved in searchTxt
    for tag in tagList:
        #print(tag, "\n")
        if 'h' in tag.name:
            typeTag = type(soup.find('li'))
            current = tag.next_sibling
            while current != None and  not isinstance(current, typeTag) and current.name not in correctName:
                current = current.next_sibling
            if current != None:
                if 'ul' in current.name or 'ol' in current.name:
                    for li in current.findAll('li'):
                        searchTxt = searchTxt + li.text
                else:
                    searchTxt = searchTxt + current.text
        #elif url extension includes the keyWord, grab all the text?
        else:
            if(tag.name in correctName):
                    searchTxt = searchTxt + tag.text
                
        return searchTxt

In [ ]:
#Applies the keyWordScraper function to a BeautifulSoup object(soup) for a list of keywords. Returns the text found.
def mapKeywordScraper(soup, keyWords):
    foundTxt = ''
    
    for keyWord in keyWords:
        foundTxt = foundTxt + str(keyWordScraper(soup, keyWord))
    #print(foundTxt)
    return foundTxt

In [ ]:
def createJsonNode():
    JSONNode = {}
    
    for x in range(0, len(keyValues)):
        print(keyValues[x], "\n")
        JSONNode[nodeParams[x]] = [mapKeywordScraper(soup, keyValues[x])]
        print(JSONNode)
    return JSONNode

In [ ]:
createJsonNode()

## CHUNKS OF CODE

In [ ]:
# Input test URL here
url = links[0]
url

In [ ]:
html_page = urllib.request.urlopen(url)
soup = BeautifulSoup(html_page, "lxml")

In [ ]:
def findTags(soup, keyWord):
    tagList = []
        
    for elem in soup(text=re.compile(keyWord)):
        tagList.append(elem.parent)
            
    return tagList

In [ ]:
tagList = findTags(soup, keyWord)

In [ ]:
searchTxt = ''
correctName = ['p', 'li', 'table', 'ul', 'ol']
tagList = findTags(soup, keyWord)
    
#This loop goes through each tag and rips the text from that tag. If that tag is a header, then the text from the next 
 #useful tag is ripped instead. All text is saved in searchTxt
for tag in tagList:
    if 'h' in tag.name:
        typeTag = type(soup.find('li'))
        current = tag.next_sibling
        while current != None and  not isinstance(current, typeTag) and current.name not in correctName:
            current = current.next_sibling
        if current != None:
            if 'ul' in current.name or 'ol' in current.name:
                for li in current.findAll('li'):
                    searchTxt = searchTxt + li.text
            else:
                searchTxt = searchTxt + current.text
    #elif url extension includes the keyWord, grab all the text?
    else:
        if(tag.name in correctName):
            searchTxt = searchTxt + tag.text
                
return searchTxt